# Data processing to create and save `count_loc_bytes_by_ip` dataframe

In [14]:
import pandas as pd
from google.colab import drive
drive.mount('/content/drive')
csv_file_path = '/content/drive/MyDrive/cybersecurity/f2301-2306.xenon.csv'
df = pd.read_csv(csv_file_path, nrows=10000000)
#df = pd.read_csv('f2301-2306.xenon.csv', nrows=100000)

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [15]:
print(df.columns)
df = df[df['Proto'] == 'tcp'].reset_index(drop=True)
current_year = pd.Timestamp.now().year
df['StartTime'] = pd.to_datetime(df['StartTime'], format='%m/%d.%H:%M:%S.%f').apply(lambda x: x.replace(year=current_year))
df['LastTime'] = pd.to_datetime(df['LastTime'], format='%m/%d.%H:%M:%S.%f').apply(lambda x: x.replace(year=current_year))
print(df)

Index(['StartTime', 'LastTime', 'Dur', 'Proto', 'SrcAddr', 'Sport', 'Dir',
       'DstAddr', 'Dport', 'TotPkts', 'State', 'SrcPkts', 'DstPkts',
       'TotBytes', 'SrcBytes', 'DstBytes', 'Mean', 'Sum', 'Min', 'Max', 'sCo',
       'dCo', 'sHops', 'dHops', 'PCRatio', 'SAppBytes', 'DAppBytes', 'Rate',
       'sMeanPktSz', 'dMeanPktSz', 'sMaxPktSz', 'dMaxPktSz', 'sMinPktSz',
       'dMinPktSz'],
      dtype='object')
                         StartTime                   LastTime        Dur  \
0       2024-12-31 16:00:00.000000 2024-12-31 16:00:02.412425   2.412425   
1       2024-12-31 16:00:00.000000 2024-12-31 16:00:03.869870   3.869870   
2       2024-12-31 16:00:00.000000 2024-12-31 16:00:01.038116   1.038116   
3       2024-12-31 16:00:11.414035 2024-12-31 16:00:11.415347   0.001312   
4       2024-12-31 16:00:00.000000 2024-12-31 16:00:11.556820  11.556820   
...                            ...                        ...        ...   
4179043 2024-01-16 08:15:45.207632 2024-01-16 08:15

In [16]:
# First, we confirm that xenon is either the src or dst IP for every row
xenon_ip = "171.64.66.201"
src_count = df[df['SrcAddr'] == xenon_ip].shape[0]
dst_count = df[df['DstAddr'] == xenon_ip].shape[0]
assert src_count + dst_count == df.shape[0]
print(src_count, '+', dst_count, '=', str(src_count + dst_count))


1262714 + 2916334 = 4179048


In [17]:
""" Find top 20 most used ports (by TotPkts whether src or dst port) and put rest of the ports in 3 buckets:
    -Well Known Ports: 0     through 1023
    -Registered Ports: 1024  through 49151
    -Dynamic Ports:    49152 through 65535 (Private)
    Create copy of df, df_top_23, with these updated ports
"""
from collections import defaultdict
from socket import getservbyname

# Function to categorize ports
def categorize_port(port) -> str:
    # get server number by port name
    if not str.isdigit(port):
        try:
            port = getservbyname(port)
        except OSError: # dstunreach, unrport, unrhpro
            return port
    else:
        port = int(port)
    # return appropriate bucket
    if port <= 1023:
        return 'WellKnown'
    elif port <= 49151:
        return 'Registered'
    elif port <= 65535:
        return 'Dynamic'
    else:
        raise ValueError("Unexpected port name: ", port)

# Identify top 20 ports by total packets (whether port was src or dst)
sport_counts = df.groupby('Sport').agg({'TotPkts': 'sum'}).reset_index()
dport_counts = df.groupby('Dport').agg({'TotPkts': 'sum'}).reset_index()
sport_counts.columns = ['Port', 'TotPkts']
dport_counts.columns = ['Port', 'TotPkts']
port_df = pd.concat([dport_counts, sport_counts], axis=0).groupby('Port').agg({'TotPkts': 'sum'}).reset_index()
port_df = port_df.sort_values(by='TotPkts', ascending=False).reset_index(drop=True)
top_20_ports_list = port_df.head(20)['Port'].tolist()
other_ports = [port for port in port_df['Port'].tolist() if port not in top_20_ports_list]

# Replace non-top 20 ports with the correct bucket
mapping = {port: categorize_port(port) for port in port_df['Port'].tolist() if port not in top_20_ports_list}
df_23_ports = df.copy()
df_23_ports['Sport'] = df_23_ports['Sport'].map(mapping).fillna(df_23_ports['Sport'])
df_23_ports['Dport'] = df_23_ports['Dport'].map(mapping).fillna(df_23_ports['Dport'])
print(df_23_ports.head(20))
print(top_20_ports_list)

                    StartTime                   LastTime        Dur Proto  \
0  2024-12-31 16:00:00.000000 2024-12-31 16:00:02.412425   2.412425   tcp   
1  2024-12-31 16:00:00.000000 2024-12-31 16:00:03.869870   3.869870   tcp   
2  2024-12-31 16:00:00.000000 2024-12-31 16:00:01.038116   1.038116   tcp   
3  2024-12-31 16:00:11.414035 2024-12-31 16:00:11.415347   0.001312   tcp   
4  2024-12-31 16:00:00.000000 2024-12-31 16:00:11.556820  11.556820   tcp   
5  2024-12-31 16:00:00.000000 2024-12-31 16:00:03.001646   3.001646   tcp   
6  2024-12-31 16:00:00.000000 2024-12-31 16:00:10.753623  10.753623   tcp   
7  2024-12-31 16:00:00.000000 2024-12-31 16:00:09.231148   9.231148   tcp   
8  2024-12-31 16:00:00.299355 2024-12-31 16:00:00.313542   0.014187   tcp   
9  2024-12-31 16:00:01.045102 2024-12-31 16:00:14.506042  13.460940   tcp   
10 2024-12-31 16:00:02.397162 2024-12-31 16:00:14.121492  11.724330   tcp   
11 2024-12-31 16:00:02.268059 2024-12-31 16:00:02.331790   0.063731   tcp   

In [18]:
"""
Creates port_bytes_by_ip dataframe:
-each row corresponds to a unique IP
-each column corresponds to one of the 20 top + 3 bucket ports
-we have two values: bytes this port and IP sends and receives (From and To)
"""

# Collect bytes from and to each port of every IP, destination and source
df_dst = df_23_ports.groupby(['DstAddr', 'Dport']).agg({'DAppBytes': 'sum', 'SAppBytes': 'sum'}).reset_index()
df_dst.columns = ['IP', 'Port', 'FromBytes', 'ToBytes']
df_src = df_23_ports.groupby(['SrcAddr', 'Dport']).agg({'SAppBytes': 'sum', 'DAppBytes': 'sum'}).reset_index()
df_src.columns = ['IP', 'Port', 'FromBytes', 'ToBytes']

# Combine data, summing rows (FromBytes and ToBytes) when IP and Port are identical
combined = pd.concat([df_dst, df_src], ignore_index=True).groupby(['IP', 'Port']).sum().reset_index()

# Pivot into table where each row is an IP, with FromBytes and ToBytes listed for each port
port_bytes_by_ip = combined.pivot_table(index='IP', columns='Port', values=['FromBytes', 'ToBytes'], aggfunc='sum').fillna(0)

# Add columns for ports if they have been left out
ordered_ports = top_20_ports_list + ['WellKnown', 'Registered', 'Dynamic'] #+ ['unrport', 'dstunreach', 'unrhpro']
current_ports = set([col[1] for col in port_bytes_by_ip.columns])
if current_ports < set(ordered_ports):
    extra_ports = set(ordered_ports) - current_ports
    extra_columns = [('FromBytes', p) for p in extra_ports] + [('ToBytes', p) for p in extra_ports]
    for column in extra_columns:
        port_bytes_by_ip[column] = 0

# Reorder columns around so top 20 ports are first in descending order
ordered_columns = [('FromBytes', p) for p in ordered_ports] + [('ToBytes', p) for p in ordered_ports]
port_bytes_by_ip = port_bytes_by_ip[ordered_columns]

# Get rid of port columns with 0 associated bytes whatsoever
pct_nonzero_cols = (port_bytes_by_ip.astype(bool).sum(axis=0) / len(port_bytes_by_ip)) * 100
zero_cols = pct_nonzero_cols[pct_nonzero_cols == 0].index.tolist()
port_bytes_by_ip.drop(columns=zero_cols, inplace=True)

# Display, save to file
print(port_bytes_by_ip)
port_bytes_by_ip.to_csv('port_bytes_by_ip.csv', index=True)


              FromBytes                                                 \
Port                ssh     imaps 52632 58044 53850 50614    http smtp   
IP                                                                       
1.116.130.171       0.0       0.0   0.0   0.0   0.0   0.0     0.0  0.0   
1.116.135.59        0.0       0.0   0.0   0.0   0.0   0.0     0.0  0.0   
1.116.137.50        0.0       0.0   0.0   0.0   0.0   0.0     0.0  0.0   
1.116.150.173       0.0       0.0   0.0   0.0   0.0   0.0     0.0  0.0   
1.116.151.108       0.0       0.0   0.0   0.0   0.0   0.0     0.0  0.0   
...                 ...       ...   ...   ...   ...   ...     ...  ...   
99.9.169.184        0.0  219654.0   0.0   0.0   0.0   0.0     0.0  0.0   
99.9.200.137        0.0       0.0   0.0   0.0   0.0   0.0     0.0  0.0   
99.93.70.131        0.0       0.0   0.0   0.0   0.0   0.0     0.0  0.0   
99.96.118.146       0.0       0.0   0.0   0.0   0.0   0.0  2937.0  0.0   
99.97.84.195      629.0       0.0   0.

In [19]:
"""
Creates count_loc_bytes_by_ip, an extension of port_bytes_by_ip
-adds a count for the frequency each IP shows up as a SrcAddr
and as a DstAddr in each row
-scores IP based on locality (Stanford, private, and rest)
"""
import ipaddress

# Collect frequency of IP (counts) for all src IPs and dst IPs
src_counts = df.groupby('SrcAddr').agg(SrcCount=('SrcAddr', 'size')).reset_index()
src_counts.rename(columns={'SrcAddr': 'IP'}, inplace=True)
dst_counts = df.groupby('DstAddr').agg(DstCount=('DstAddr', 'size')).reset_index()
dst_counts.rename(columns={'DstAddr': 'IP'}, inplace=True)

# Merge source and destination counts for each IP; if only one exists make other 0
src_dst_counts = pd.merge(src_counts, dst_counts, on='IP', how='outer').set_index('IP')
src_dst_counts.fillna(0, inplace=True)

# Define Stanford's private and public subnetworks (to categorize IPs)
stanford_private_subnets = [
    ipaddress.ip_network('10.0.0.0/8'),
    ipaddress.ip_network('172.16.0.0/12'),
    ipaddress.ip_network('192.168.0.0/16')
]
stanford_public_subnets = [
    ipaddress.ip_network('128.12.0.0/16'),
    ipaddress.ip_network('171.64.0.0/14'),
    ipaddress.ip_network('204.63.224.0/21'),
]

# Assign locality: 1 for stanford private, 2 for stanford public, 3 for internet-at-large
def check_locality(ip):
    ip_addr = ipaddress.ip_address(ip)
    if any(ip_addr in subnet for subnet in stanford_private_subnets):
      return 1
    elif any(ip_addr in subnet for subnet in stanford_public_subnets):
      return 2
    else:
      return 3

# Add Locality, SrcCount, and DstCount to port_bytes_by_ip dataframe
count_loc_bytes_by_ip = port_bytes_by_ip.copy()
ip_locality = count_loc_bytes_by_ip.index.to_series().apply(check_locality)
count_loc_bytes_by_ip.insert(0, 'Locality', ip_locality)
count_loc_bytes_by_ip.insert(0, 'DstCount', src_dst_counts['DstCount'])
count_loc_bytes_by_ip.insert(0, 'SrcCount', src_dst_counts['SrcCount'])

# Display and save for later
print(count_loc_bytes_by_ip.groupby('Locality').agg(NumLoc=(( 'Locality',           ''), 'size')))
count_loc_bytes_by_ip.to_parquet('/content/drive/MyDrive/cybersecurity/count_loc_bytes_by_ip.parquet')


          NumLoc
Locality        
1            333
2             28
3          74647


# Load `count_loc_bytes_by_ip` from file and start visualizations

In [2]:
import pandas as pd
import numpy as np
import ast
from google.colab import drive

try:
  count_loc_bytes_by_ip
  print("count_loc_bytes_by_ip exists already")
except NameError:
  print("loading count_loc_bytes_by_ip from drive")
  drive.mount('/content/drive', force_remount=True)
  count_loc_bytes_by_ip = pd.read_parquet('/content/drive/MyDrive/cybersecurity/count_loc_bytes_by_ip.parquet')

print(count_loc_bytes_by_ip)


loading count_loc_bytes_by_ip from drive
Mounted at /content/drive
              SrcCount DstCount Locality FromBytes                        \
Port                                           ssh     imaps 52632 58044   
IP                                                                         
1.116.130.171      1.0      0.0        3       0.0       0.0   0.0   0.0   
1.116.135.59       1.0      0.0        3       0.0       0.0   0.0   0.0   
1.116.137.50       2.0      0.0        3       0.0       0.0   0.0   0.0   
1.116.150.173      2.0      0.0        3       0.0       0.0   0.0   0.0   
1.116.151.108      2.0      0.0        3       0.0       0.0   0.0   0.0   
...                ...      ...      ...       ...       ...   ...   ...   
99.9.169.184     182.0      9.0        3       0.0  219654.0   0.0   0.0   
99.9.200.137       1.0      0.0        3       0.0       0.0   0.0   0.0   
99.93.70.131       1.0      0.0        3       0.0       0.0   0.0   0.0   
99.96.118.146      4.

In [3]:
"""
Creates ip_summary_df for visualizing IP info in plots
-SrcCount, DstCount, Locality from count_loc_bytes_by_ip
-Top 1 and 2 ports for each IP by bytes, FromBytes and ToBytes combined
-Associated FromBytes and ToBytes for each of TopPort1 and TopPort2
"""
# Create
port_bytes_by_ip = count_loc_bytes_by_ip.drop(columns=[( 'SrcCount', ''), ( 'DstCount', ''), ( 'Locality', '')])
ip_summary_df = count_loc_bytes_by_ip[[('SrcCount', ''), ('DstCount', ''), ('Locality', '')]].copy()
ip_summary_df.columns = ip_summary_df.columns.get_level_values(0)

# Identify top 2 ports for all IPs and add to dataframe
combined_bytes = (port_bytes_by_ip['FromBytes'].values + port_bytes_by_ip['ToBytes'].values)
top_indices = np.argsort(-combined_bytes, axis=1)[:, :2]
top_ports = np.array(port_bytes_by_ip['FromBytes'].columns)[top_indices]
ip_summary_df['TopPort1'] = top_ports[:, 0]
ip_summary_df['TopPort2'] = top_ports[:, 1]

# Restructure port_bytes_by_ip s.t. it is indexed by IP and Port
port_bytes_by_ip.columns = pd.MultiIndex.from_tuples(port_bytes_by_ip.columns)
port_bytes_long = port_bytes_by_ip.stack(level=1).reset_index()
port_bytes_long.columns = ['IP', 'Port', 'FromBytes', 'ToBytes']

# Merge relevant columns of port_bytes_long (FromBytes and ToBytes) where IP and Port (top 1) match
merged_topport1 = pd.merge(ip_summary_df, port_bytes_long, how='left', left_on=['IP', 'TopPort1'], right_on=['IP', 'Port'])
merged_topport1 = merged_topport1.rename(columns={'FromBytes': 'FromBytes1', 'ToBytes': 'ToBytes1'})
merged_topport1 = merged_topport1.drop(columns=['Port'])

# Perform the same merge where IP and Port (top 2) match
merged_topport2 = pd.merge(merged_topport1, port_bytes_long, how='left', left_on=['IP', 'TopPort2'], right_on=['IP', 'Port'])
merged_topport2 = merged_topport2.rename(columns={'FromBytes': 'FromBytes2', 'ToBytes': 'ToBytes2'})
ip_summary_df = merged_topport2.drop(columns=['Port'])

print(ip_summary_df)

                  IP  SrcCount  DstCount  Locality TopPort1 TopPort2  \
0      1.116.130.171       1.0       0.0         3      ssh    imaps   
1       1.116.135.59       1.0       0.0         3      ssh    imaps   
2       1.116.137.50       2.0       0.0         3      ssh    imaps   
3      1.116.150.173       2.0       0.0         3      ssh    imaps   
4      1.116.151.108       2.0       0.0         3      ssh    imaps   
...              ...       ...       ...       ...      ...      ...   
75003   99.9.169.184     182.0       9.0         3    imaps  Dynamic   
75004   99.9.200.137       1.0       0.0         3      ssh    imaps   
75005   99.93.70.131       1.0       0.0         3      ssh    imaps   
75006  99.96.118.146       4.0       0.0         3     http      ssh   
75007   99.97.84.195       2.0       0.0         3      ssh    imaps   

       FromBytes1   ToBytes1  FromBytes2  ToBytes2  
0             0.0        0.0         0.0       0.0  
1             0.0        0.0 

In [10]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.preprocessing import StandardScaler

count_and_bytes_by_ip = count_loc_bytes_by_ip.drop(columns=[('Locality', '')], errors='ignore')
pct_nonzero_rows = (port_bytes_by_ip.ne(0).sum(axis=1) / port_bytes_by_ip.shape[1]) * 100
nonzero_mask = pct_nonzero_rows != 0
count_and_bytes_by_ip = count_and_bytes_by_ip[nonzero_mask]
count_and_bytes_by_ip = count_and_bytes_by_ip.apply(lambda x: x / x[x > 0].min(), axis=0)
count_and_bytes_by_ip = np.log1p(count_and_bytes_by_ip)
min_nonzero = count_and_bytes_by_ip.apply(lambda x: x[x > 0].min())
min_nonzero_df = pd.DataFrame(min_nonzero, columns=['min_nonzero']).T
desc_stats = count_and_bytes_by_ip.describe()
custom_stats = pd.concat([desc_stats, min_nonzero_df])

print(custom_stats)

#df1 = pd.DataFrame(count_and_bytes_by_ip, index=count_loc_bytes_by_ip.index)
#df2 = pd.concat([df1.loc['1.46.158.252',], df1.loc['1.46.21.174',], pd.DataFrame(list(count_loc_bytes_by_ip.columns))], axis=1)
#print(df2)
#print(list(count_loc_bytes_by_ip.columns))
#print(df1.loc['1.46.158.252',])
#print(df1.loc['1.46.21.174',])

                 SrcCount      DstCount     FromBytes                \
Port                                              ssh         imaps   
count        43491.000000  43491.000000  43491.000000  43491.000000   
mean             2.100571      0.094778      0.158889      0.346867   
std              1.059698      0.567728      0.932273      1.552814   
min              0.000000      0.000000      0.000000      0.000000   
25%              1.098612      0.000000      0.000000      0.000000   
50%              1.945910      0.000000      0.000000      0.000000   
75%              2.833213      0.000000      0.000000      0.000000   
max             14.048775     14.885838     24.132685     22.314805   
min_nonzero      0.693147      0.693147      0.693147      0.693147   

                                                                     \
Port                52632         58044         53850         50614   
count        43491.000000  43491.000000  43491.000000  43491.000000   
mean 

In [48]:

"""
# Testing out different scalers / logs for different parts of data
from sklearn.preprocessing import StandardScaler

test = count_loc_bytes_by_ip.copy()
test['FromBytes'] = np.log(test['FromBytes'] + 0.0001)
test['ToBytes'] = np.log(test['ToBytes'] + 0.0001)
test['SrcCount'] = np.log(test['SrcCount'] + 1)
test['DstCount'] = np.log(test['DstCount'] + 1)
scaler = StandardScaler()
test = pd.DataFrame(scaler.fit_transform(test))
print(test.describe())"""

                 0             1             2             3             4   \
count  7.500800e+04  7.500800e+04  7.500800e+04  7.500800e+04  7.500800e+04   
mean   6.384730e-17  6.820483e-18  2.300018e-16  1.667229e-17  3.334458e-17   
std    1.000007e+00  1.000007e+00  1.000007e+00  1.000007e+00  1.000007e+00   
min   -1.701852e+00 -1.479555e-01 -1.481932e+01 -1.353789e-01 -1.789358e-01   
25%   -6.958212e-01 -1.479555e-01  6.887536e-02 -1.353789e-01 -1.789358e-01   
50%   -2.280436e-01 -1.479555e-01  6.887536e-02 -1.353789e-01 -1.789358e-01   
75%    6.469456e-01 -1.479555e-01  6.887536e-02 -1.353789e-01 -1.789358e-01   
max    1.116301e+01  3.213594e+01  6.887536e-02  1.150289e+01  7.909838e+00   

                 5             6             7             8             9   \
count  7.500800e+04  7.500800e+04  7.500800e+04  7.500800e+04  7.500800e+04   
mean   2.143242e-18  4.156232e-18  5.210091e-18  1.409093e-18  3.940723e-17   
std    1.000007e+00  1.000007e+00  1.000007e+00  1.

In [12]:
from sklearn.cluster import OPTICS
from sklearn.preprocessing import StandardScaler
import plotly.express as px
import time

# Drop the 'Locality' column, remove zero-data IPs
count_and_bytes_by_ip = count_loc_bytes_by_ip.drop(columns=[('Locality', '')], errors='ignore')
pct_nonzero_rows = (port_bytes_by_ip.ne(0).sum(axis=1) / port_bytes_by_ip.shape[1]) * 100
nonzero_mask = pct_nonzero_rows != 0
count_and_bytes_by_ip = count_and_bytes_by_ip[nonzero_mask]

# Scale data using log(1 + x / x_1) where x_1 is the minimum nonzero value in column x
count_and_bytes_by_ip = count_and_bytes_by_ip.apply(lambda x: x / x[x > 0].min(), axis=0)
count_and_bytes_by_ip = np.log1p(count_and_bytes_by_ip)

# Normalize data (skipping to retain 0 values and because std dev is meaningless)
scaler = StandardScaler()
count_and_bytes_by_ip = scaler.fit_transform(count_and_bytes_by_ip)

# Fit the OPTICS model
start_time = time.time()
optics_model = OPTICS(min_samples=10, xi=0.01, min_cluster_size=0.03)
optics_model.fit(count_and_bytes_by_ip)
print("Time taken for OPTICS:", time.time() - start_time)

# Plot reachability
ip_summary_df.set_index('IP', inplace=True)
ip_summary_df = ip_summary_df[nonzero_mask]
reachability = optics_model.reachability_[optics_model.ordering_]
reachability = np.where(np.isinf(reachability), 10, reachability)  # Replace inf with 10
ip_summary_df['Reachability'] = np.log(reachability + 0.0001)
stats = ip_summary_df['Reachability'].describe()
print(stats)
ip_summary_df['Label'] = optics_model.labels_[optics_model.ordering_].astype(str)
ip_summary_df['Space'] = np.arange(len(count_and_bytes_by_ip))
ip_summary_df.reset_index(inplace=True)

fig = px.scatter(
    ip_summary_df,
    x='Space',
    y='Reachability',
    color='Label',
    hover_data={'IP': True, 'Label': True, 'TopPort1': True, 'TopPort2': True, 'FromBytes1': True, 'ToBytes1': True, 'FromBytes2': True, 'ToBytes2': True},
    title='Reachability plot after OPTICS with Hover'
)
fig.update_traces(marker=dict(opacity=0.7))
fig.update_layout(width=800)
fig.show()

/usr/local/lib/python3.10/dist-packages/sklearn/cluster/_optics.py:995: RuntimeWarning:

divide by zero encountered in divide

<ipython-input-12-55c4fe97b4bb>:30: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.



Time taken for OPTICS: 173.0567066669464
count    43491.000000
mean        -3.666589
std          2.728559
min         -9.210340
25%         -4.469190
50%         -2.692485
75%         -1.966719
max          3.812222
Name: Reachability, dtype: float64


In [1]:
count_and_bytes_by_ip

NameError: name 'count_and_bytes_by_ip' is not defined

<ipython-input-50-c0138d429b7b>:4: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.



count    43491.000000
mean        -6.080755
std          2.160615
min         -9.210340
25%         -7.528854
50%         -5.935002
75%         -4.971834
max          5.948058
Name: Reachability, dtype: float64


# Old stuff (ignore)

In [ ]:
"""
Perform UMAP and create summary table with UMAP 2-D columns, cluster labels, IP as index
"""

!pip install umap-learn
import umap.umap_ as umap
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
import plotly.express as px

# Reduce count_hops_bytes_by_ip data to 2D
reducer = umap.UMAP(min_dist=0.1, n_components=2, n_neighbors=40)
ip_summary_embedding = reducer.fit_transform(count_and_bytes_by_ip)
ip_summary_df = pd.DataFrame(ip_summary_embedding, columns=['UMAP_1', 'UMAP_2'], index=count_and_bytes_by_ip.index)
ip_summary_df['Label'] = optics_model.labels_
ip_summary_df = ip_summary_df.reset_index(drop=False)
print(ip_summary_embedding.shape)
print(ip_summary_df)


In [ ]:
from sklearn.cluster import DBSCAN
from sklearn.preprocessing import StandardScaler
import numpy as np

"""
# Properly scale and perform DBSCAN on count_hops_bytes_by_ip
scaler = StandardScaler()
count_hops_bytes_by_ip_S = scaler.fit_transform(count_hops_bytes_by_ip)
clustering = DBSCAN(eps=0.5).fit(count_hops_bytes_by_ip_S)

# Add labels from clustering to a copy of count_hops_bytes_by_ip
count_hops_bytes_by_ip_L = count_hops_bytes_by_ip.copy()
count_hops_bytes_by_ip_L['Label'] = clustering.labels_

print(np.unique(clustering.labels_))

"""

# Assuming count_hops_bytes_by_ip is your DataFrame
batch_size = 10000
num_batches = int(np.ceil(len(count_loc_bytes_by_ip) / batch_size))

all_labels = []

for i in range(num_batches):
    batch = count_hops_bytes_by_ip[i*batch_size:(i+1)*batch_size]

    # Standardize the batch data
    scaler = StandardScaler()
    scaled_batch = scaler.fit_transform(batch)

    # Perform DBSCAN clustering on the batch
    clustering = DBSCAN(eps=0.5).fit(scaled_batch)

    # Collect labels
    all_labels.extend(clustering.labels_)

# Add collected labels to the DataFrame
count_hops_bytes_by_ip_L = count_hops_bytes_by_ip.copy()
count_hops_bytes_by_ip_L['Label'] = all_labels

print(np.unique(count_hops_bytes_by_ip_L['Label']))


In [ ]:
!pip install umap-learn
import umap.umap_ as umap
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
import plotly.express as px

# Reduce count_hops_bytes_by_ip data to 2D
reducer = umap.UMAP(min_dist=0.1, n_components=2, n_neighbors=40)
ip_summary_data = StandardScaler().fit_transform(count_hops_bytes_by_ip)
ip_summary_embedding = reducer.fit_transform(ip_summary_data)
ip_summary_df = pd.DataFrame(ip_summary_embedding, columns=['UMAP_1', 'UMAP_2'], index=count_hops_bytes_by_ip.index)
ip_summary_df['Label'] = count_hops_bytes_by_ip_L['Label']
ip_summary_df = ip_summary_df.reset_index(drop=False)
print(ip_summary_embedding.shape)

In [ ]:
ip_summary_df_saved = ip_summary_df.copy()

In [ ]:
"""
Adds 4 columns to ip_summary_df
-Top 1 and 2 ports for each IP by bytes, FromBytes and ToBytes combined
associated From/To Bytes
-Associated FromBytes and ToBytes for each of TopPort1 and TopPort2
"""

# Identify top 2 ports for all IPs and add to dataframe
ip_summary_df = ip_summary_df_saved.copy()
combined_bytes = (port_bytes_by_ip['FromBytes'].values + port_bytes_by_ip['ToBytes'].values)
top_indices = np.argsort(-combined_bytes, axis=1)[:, :2]
top_ports = np.array(port_bytes_by_ip['FromBytes'].columns)[top_indices]
ip_summary_df['TopPort1'] = top_ports[:, 0]
ip_summary_df['TopPort2'] = top_ports[:, 1]

# Restructure port_bytes_by_ip s.t. it is indexed by IP and Port
port_bytes_by_ip.columns = pd.MultiIndex.from_tuples(port_bytes_by_ip.columns)
port_bytes_long = port_bytes_by_ip.stack(level=1, future_stack=True).reset_index()
port_bytes_long.columns = ['IP', 'Port', 'FromBytes', 'ToBytes']

# Merge relevant columns of port_bytes_long (FromBytes and ToBytes) where IP and Port (top 1) match
merged_topport1 = pd.merge(ip_summary_df, port_bytes_long, how='left', left_on=['IP', 'TopPort1'], right_on=['IP', 'Port'])
merged_topport1 = merged_topport1.rename(columns={'FromBytes': 'FromBytes1', 'ToBytes': 'ToBytes1'})
merged_topport1 = merged_topport1.drop(columns=['Port'])

# Perform the same merge where IP and Port (top 2) match
merged_topport2 = pd.merge(merged_topport1, port_bytes_long, how='left', left_on=['IP', 'TopPort2'], right_on=['IP', 'Port'])
merged_topport2 = merged_topport2.rename(columns={'FromBytes': 'FromBytes2', 'ToBytes': 'ToBytes2'})
ip_summary_df = merged_topport2.drop(columns=['Port'])

print(ip_summary_df)

In [ ]:
import plotly.io as pio
# pio.renderers
pio.renderers.default = "iframe"

# Plot with hovering data (first 100 rows)
ip_summary_df['IP'] = ip_summary_df['IP'].astype(str)
ip_summary_df['TopPort1'] = ip_summary_df['TopPort1'].astype(str)
ip_summary_df['TopPort2'] = ip_summary_df['TopPort2'].astype(str)
ip_summary_df['Label'] = ip_summary_df['Label'].astype(str)

fig = px.scatter(
    ip_summary_df,
    x='UMAP_1',
    y='UMAP_2',
    color='Label',
    hover_data={'IP': True, 'UMAP_1': False, 'UMAP_2': False, 'Label': True, 'TopPort1': True, 'TopPort2': True, 'FromBytes1': True, 'ToBytes1': True, 'FromBytes2': True, 'ToBytes2': True},
    title='UMAP projection of IP count, hops, bytes per port'
)
fig.update_traces(marker=dict(opacity=0.7))
fig.update_layout(width=800)
fig.show()

In [ ]:
#import seaborn as sns
#import matplotlib.pyplot as plt

# Create color mapping for each label value
#unique_labels = np.unique(clustering.labels_)
#n_unique_labels = len(unique_labels)
#color_map = plt.cm.get_cmap('tab20', n_unique_labels)
#colors = color_map(np.linspace(0, 1, n_unique_labels))
#color_dict = {label: colors[i] for i, label in enumerate(unique_labels)}



"""
# Generate scatterplot of UMAP with labels from DBSCAN
plt.scatter(
    ip_summary_embedding[:, 0],
    ip_summary_embedding[:, 1],
    c= count_hops_bytes_by_ip_L['Label'].map(color_dict),
    alpha=0.7
)
plt.gca().set_aspect('equal', 'datalim')
plt.title('UMAP projection of IP count, hops, bytes per port', fontsize=13);
"""

In [ ]:
# Notes:
# -appbytes
# -sport to dport done
# -only tcp done
# -interactive plotly: https://plotly.com/python/hover-text-and-formatting/
# -replace hops w/ local v. non-local

"""
Experimenting with OPTICS clustering on counts_hops_bytes_by_ip

from sklearn.cluster import OPTICS
import matplotlib.pyplot as plt
import numpy as np

optics_model = OPTICS(min_samples=5, xi=0.05, min_cluster_size=0.1)
optics_model.fit(count_hops_bytes_by_ip)
labels = optics_model.labels_
reachability = optics_model.reachability_
count_hops_bytes_by_ip['cluster'] = labels


# Plot the reachability plot
plt.figure(figsize=(10, 7))
space = np.arange(len(count_hops_bytes_by_ip))
plt.plot(space, reachability[optics_model.ordering_], 'g.', alpha=0.5)
plt.title('Reachability Plot')
plt.ylabel('Reachability Distance')
plt.show()

# Scatter plot of the clustered data (for the first two dimensions)
plt.figure(figsize=(10, 7))
plt.scatter(count_hops_bytes_by_ip[:, 0], count_hops_bytes_by_ip[:, 1], c=labels, cmap='rainbow', alpha=0.7)
plt.title('OPTICS Clustering')
plt.xlabel('Count')
plt.ylabel('Hops')
plt.show()
"""



In [ ]:
def volume_through_ip(df, sortby='packets'):
    # Aggregate packet and byte counts for source and dest IPs separately
    src_volume = df.groupby('SrcAddr').agg({'SrcPkts': 'sum', 'SrcBytes': 'sum'}).reset_index()
    dst_volume = df.groupby('DstAddr').agg({'DstPkts': 'sum', 'DstBytes': 'sum'}).reset_index()

    # Merge both counts and sum appropriately
    src_volume = src_volume.rename(columns={'SrcAddr': 'IP', 'SrcPkts': 'Pkts', 'SrcBytes': 'Bytes'})
    dst_volume = dst_volume.rename(columns={'DstAddr': 'IP', 'DstPkts': 'Pkts', 'DstBytes': 'Bytes'})
    merged_volume = pd.merge(src_volume, dst_volume, on='IP', how='outer', suffixes=('_Src', '_Dst'))
    merged_volume = merged_volume.fillna(0)
    merged_volume['TotalPkts'] = merged_volume['Pkts_Src'] + merged_volume['Pkts_Dst']
    merged_volume['TotalBytes'] = merged_volume['Bytes_Src'] + merged_volume['Bytes_Dst']

    # Return relevant columns sorted by packets
    final_volume = merged_volume[['IP', 'TotalPkts', 'TotalBytes']]
    sort = 'TotalPkts' if sortby == 'packets' else 'TotalBytes'
    final_volume = final_volume.sort_values(by=sort, ascending=False).reset_index(drop=True)
    return final_volume

print(volume_through_ip(df))


Stats are going to be grouped by time, such as daily and weekly statistics for connection between two IPs.

In [ ]:
# Statistics on source's port use
def port_use(df, ip, dest = None, granularity='date'):
    filtered_df = df.loc[df['SrcAddr'] == ip].copy()
    if dest is not None:
        filtered_df = filtered_df[filtered_df['DstAddr'] == dest]

    # Extract time attribute based on granularity
    if granularity == 'date':
        filtered_df['Time'] = filtered_df['StartTime'].dt.date
    elif granularity == 'hour':
        filtered_df['Time'] = filtered_df['StartTime'].dt.floor('H')
    elif granularity == 'minute':
        filtered_df['Time'] = filtered_df['StartTime'].dt.floor('min')
    else:
        raise ValueError("Granularity must be 'date', 'hour', or 'minute'")

    # Create table: rows=each time frame, cols=count of each port in that time frame
    grouped = filtered_df.groupby(['Time', 'Sport']).size().reset_index(name='Count')
    pivot_table = grouped.pivot(index='Time', columns='Sport', values='Count').fillna(0)

    # Add row for Total Port Use and column for Total Time Use
    total_row = pivot_table.sum().to_frame().T
    total_row.index = ['TotPortUse']
    pivot_table = pd.concat([total_row, pivot_table])
    pivot_table['TotTimeUse'] = pivot_table.sum(axis=1)

    # Return table with most used ports first
    pivot_table = pivot_table.T.sort_values(by='TotPortUse', ascending=False)
    return pivot_table.T

"""
# Driver
first_src_addr = df['SrcAddr'].iloc[0]
first_dst_addr = df['DstAddr'].iloc[0]

frequencies = port_use(df, first_src_addr, None, "minute")
probabilities = frequencies.div(frequencies['TotTimeUse'], axis=0)
probabilities.drop(columns='TotTimeUse', inplace=True)
print(probabilities)
"""

In [ ]:
import umap.umap_ as umap
import matplotlib.pyplot as plt
import seaborn as sns

reducer = umap.UMAP()
embedding = reducer.fit_transform(probabilities)
print(embedding)

plt.scatter(
    embedding[:, 0],
    embedding[:, 1],
)
plt.gca().set_aspect('equal', 'datalim')
plt.title('UMAP projection of port probabilities', fontsize=24)

In [ ]:
# Average outgoing packets frome one source address
def packets_sent(df, ip, dest = None, granularity='date'):
    filtered_df = df[df['SrcAddr'] == ip]
    if dest is not None:
        filtered_df = filtered_df[filtered_df['DstAddr'] == dest]

    # Extract time attribute based on granularity
    if granularity == 'date':
        filtered_df['Time'] = filtered_df['StartTime'].dt.date
    elif granularity == 'hour':
        filtered_df['Time'] = filtered_df['StartTime'].dt.floor('H')
    elif granularity == 'minute':
        filtered_df['Time'] = filtered_df['StartTime'].dt.floor('min')
    else:
        raise ValueError("Granularity must be 'date', 'hour', or 'minute'")

    # Group by the time attribute
    grouped_df = filtered_df.groupby(['Time', 'Sport']).agg(
        packets_sent=('TotPkts', 'sum'),
        num_connections=('TotPkts', 'count')
    ).reset_index()

    # Calculate the average packets per connection (use 0 instead of NaN)
    grouped_df['avg_packets'] = grouped_df.apply(
        lambda row: row['packets_sent'] / row['num_connections'] if row['num_connections'] > 0 else 0,
        axis=1
    )
    pivot_df = grouped_df.pivot(index='Time', columns='Sport', values='avg_packets').fillna(0).reset_index()

    # Add total row and column
    # Calculate the overall average packets per port across all time
    overall_avg_packets = grouped_df.groupby('Sport').agg(
        overall_avg_packets=('avg_packets', 'mean')
    ).T

    # Convert the series to a DataFrame with 'Time' as 'Average'
    overall_avg_packets_df = overall_avg_packets.reset_index(drop=True)
    overall_avg_packets_df['Time'] = 'Average'

    # Rearrange columns to match pivot_df
    overall_avg_packets_df = overall_avg_packets_df[['Time'] + list(overall_avg_packets.columns)]

    # Concatenate the average row with the final DataFrame
    final_df = pd.concat([overall_avg_packets_df, pivot_df], ignore_index=True)

    # Sort the columns in descending order of the top row (overall average per port)
    sorted_columns = ['Time'] + overall_avg_packets_df.iloc[0, 1:].sort_values(ascending=False).index.tolist()
    final_df = final_df[sorted_columns]
    return final_df

print(packets_sent(df, first_src_addr, None, granularity='minute'))

In [ ]:
def duration(df, ip, granularity='minute'):
    # Sum of each port's durations for all connections within each time interval
    filtered_df = df[df['SrcAddr'] == ip]

    # Extract time attribute based on granularity
    if granularity == 'date':
        filtered_df['Time'] = filtered_df['StartTime'].dt.date
    elif granularity == 'hour':
        filtered_df['Time'] = filtered_df['StartTime'].dt.floor('H')
    elif granularity == 'minute':
        filtered_df['Time'] = filtered_df['StartTime'].dt.floor('min')
    else:
        raise ValueError("Granularity must be 'date', 'hour', or 'minute'")

    # Group by the time attribute
    grouped_df = filtered_df.groupby(['Time', 'Sport']).agg(
        duration=('Dur', 'sum'),
    ).reset_index()

    total_df = filtered_df.groupby('Time').agg(
        duration=('Dur', sum)
    ).reset_index()
    return grouped_df

print(duration(df, first_src_addr, 'minute'))


In [ ]:
# Average number of packets between two addresses
def daily_avg_packets(src_addr, dst_addr):
    filtered_df = df[df['SrcAddr'] == src_addr & df['DstAddr'] == dst_addr]
    filtered_df['Date'] = filtered_df.dt.date

    daily_stats = filtered_df.groupby('Date').agg(
        packets_sent=pd.NamedAgg(column='Packets', aggfunc='sum'),
        num_connections=pd.NamedAgg(column='SrcAddr', aggfunc='count')
    ).reset_index()


    # Want dataframe with columns: Date, packets sent on this date, num connections, average
# Driver
src_addr = df['SrcAddr'].iloc[0]
dst_addr = df['DstAddr'].iloc[0]
print(daily_avg_packets(src_addr, dst_addr))

